In [1]:
import sys, time
import numpy as np
sys.path.append('/hosthome/tango/tangostationcontrol/tangostationcontrol')
from toolkit.archiver import *
from matplotlib import pyplot as plt

In [2]:
# Apply the chosen JSON configuration file in directory toolkit/archiver_config/
archiver = Archiver(selector_filename='lofar2.json')

Attribute stat/recv/1/version_r not found in archiving list!
Attribute stat/recv/1/opcua_missing_attributes_r not found in archiving list!
Attribute stat/recv/1/ant_status_r not found in archiving list!
Attribute stat/recv/1/rcu_led_colour_r not found in archiving list!
Attribute stat/recv/1/ant_mask_rw removed!
Attribute stat/recv/1/hbat_bf_delays_r not found in archiving list!
Attribute stat/recv/1/hbat_bf_delays_rw not found in archiving list!
Attribute stat/recv/1/hbat_led_on_r not found in archiving list!
Attribute stat/recv/1/hbat_led_on_rw not found in archiving list!
Attribute stat/recv/1/hbat_pwr_lna_on_r not found in archiving list!
Attribute stat/recv/1/hbat_pwr_lna_on_rw not found in archiving list!
Attribute stat/recv/1/hbat_pwr_on_r not found in archiving list!
Attribute stat/recv/1/hbat_pwr_on_rw not found in archiving list!
Attribute stat/recv/1/rcu_adc_locked_r not found in archiving list!
Attribute stat/recv/1/rcu_attenuator_db_r not found in archiving list!
Attribute

In [3]:
# Print the configuration file (as a dictionary)
selector = archiver.selector
print(selector.filename)
env_dict = selector.get_dict()
env_dict

lofar2.json


{'global_variables': {'development_polling_time': '10000',
  'development_archive_time': '60000'},
 'devices': {'STAT/RECV/1': {'environment': 'development',
   'include': [],
   'exclude': ['CLK_Enable_PWR_R',
    'CLK_I2C_STATUS_R',
    'CLK_PLL_error_R',
    'CLK_PLL_locked_R',
    'CLK_translator_busy_R']},
  'STAT/SDP/1': {'environment': 'development',
   'include': [],
   'exclude': ['FPGA_scrap_R', 'FPGA_scrap_RW']},
  'STAT/SST/1': {'environment': 'development', 'include': [], 'exclude': []},
  'STAT/XST/1': {'environment': 'development', 'include': [], 'exclude': []},
  'STAT/UNB2/1': {'environment': 'development', 'include': [], 'exclude': []}}}

In [4]:
device_name = 'STAT/RECV/1'
d=DeviceProxy(device_name) 
d.set_timeout_millis(10000)
state = str(d.state())
print(state)

OFF


In [5]:
# Add RECV attributes to perform load test
archiver.add_attributes_by_device(device_name,global_archive_period=5000)

Attribute stat/recv/1/version_r will not be archived because polling is set to FALSE!
Attribute stat/recv/1/opcua_missing_attributes_r will not be archived because polling is set to FALSE!
Attribute stat/recv/1/ant_status_r will not be archived because polling is set to FALSE!
Attribute stat/recv/1/rcu_led_colour_r will not be archived because polling is set to FALSE!
Attribute stat/recv/1/hbat_bf_delays_r will not be archived because polling is set to FALSE!
Attribute stat/recv/1/hbat_bf_delays_rw will not be archived because polling is set to FALSE!
Attribute stat/recv/1/hbat_led_on_r will not be archived because polling is set to FALSE!
Attribute stat/recv/1/hbat_led_on_rw will not be archived because polling is set to FALSE!
Attribute stat/recv/1/hbat_pwr_lna_on_r will not be archived because polling is set to FALSE!
Attribute stat/recv/1/hbat_pwr_lna_on_rw will not be archived because polling is set to FALSE!
Attribute stat/recv/1/hbat_pwr_on_r will not be archived because polling

In [6]:
# Print the errors for each attribute
# If the device is in OFF state, all its attributes should be in error (normal behaviour)
err_dict = archiver.get_subscriber_errors()
err_dict

{'tango://databaseds:10000/stat/recv/1/ant_mask_rw': 'Read value for attribute ANT_mask_RW has not been updated',
 'tango://databaseds:10000/stat/recv/1/rcu_mask_rw': 'Read value for attribute RCU_mask_RW has not been updated',
 'tango://databaseds:10000/stat/recv/1/status': 'Storing Error: mysql_stmt_bind_param() failed, err=Buffer type is not supported'}

In [7]:
# Start the device
if state == "OFF":
    time.sleep(1)
    d.initialise()
    time.sleep(1)
state = str(d.state())
if state == "STANDBY":
    d.set_defaults()
    d.on()
state = str(d.state())
if state == "ON":
    print("Device is now in ON state")

Device is now in ON state


In [8]:
# Print the attributes currently managed by the event subscriber
attrs = archiver.get_subscriber_attributes()
attrs

['tango://databaseds:10000/stat/recv/1/ant_mask_rw',
 'tango://databaseds:10000/stat/recv/1/rcu_mask_rw',
 'tango://databaseds:10000/stat/recv/1/state',
 'tango://databaseds:10000/stat/recv/1/status']

In [9]:
# Print the errors for each attribute
err_dict = archiver.get_subscriber_errors()
err_dict

{'tango://databaseds:10000/stat/recv/1/ant_mask_rw': 'Read value for attribute ANT_mask_RW has not been updated',
 'tango://databaseds:10000/stat/recv/1/rcu_mask_rw': 'Read value for attribute RCU_mask_RW has not been updated',
 'tango://databaseds:10000/stat/recv/1/status': 'Storing Error: mysql_stmt_bind_param() failed, err=Buffer type is not supported'}

In [10]:
# Print the attribute periods
def print_periods(attrs):
    print("{:<45} {:<15} {:<15}".format('Attribute','Poll Period','Archive Period'))
    print("----------")
    for a in attrs:
        a = parse_attribute_name(a)
        ap = AttributeProxy(a)
        att_fqname = ap.get_device_proxy().name()+'/'+ap.name()
        print("{:<45} {:<15} {:<15}".format(att_fqname,ap.get_poll_period(),ap.get_property('archive_period')['archive_period'][0],sep='\t'))

attrs = archiver.get_subscriber_attributes()
print_periods(attrs)

Attribute                                     Poll Period     Archive Period 
----------
STAT/RECV/1/ant_mask_rw                       1000            5000           
STAT/RECV/1/rcu_mask_rw                       1000            5000           
STAT/RECV/1/state                             1000            5000           
STAT/RECV/1/status                            1000            5000           


In [11]:
# Print the current event subscriber archive frequency (number of total archive events per minute)
# Be aware that these statistics need some time (even minutes) since the device initialization to be reliable
archiver.get_subscriber_load()

'0.0 events/period'

In [12]:
# Print the current attribute archive frequency (number of events per minute)
# E.G. if an attribute is supposed to be archived every 10s, its frequency value should be 6
def print_freq(attrs):
    print("{:<45} {:<15} {:<15}".format('Attribute','Record Freq','Failure Freq'))
    print("----------")
    for a in attrs:
        a = parse_attribute_name(a)
        ap = AttributeProxy(a)
        att_fqname = ap.get_device_proxy().name()+'/'+ap.name()
        print("{:<45} {:<15} {:<15}".format(att_fqname,archiver.get_attribute_freq(att_fqname),archiver.get_attribute_failures(att_fqname)))

attrs = archiver.get_subscriber_attributes()
print_freq(attrs)

Attribute                                     Record Freq     Failure Freq   
----------
STAT/RECV/1/ant_mask_rw                       0.0             12.0           
STAT/RECV/1/rcu_mask_rw                       0.0             12.0           
STAT/RECV/1/state                             0.0             12.0           
STAT/RECV/1/status                            0.0             12.0           


In [13]:
# Update the archive time of an attribute
archiver.update_archiving_attribute('STAT/RECV/1/rcu_mask_rw',polling_period=1000,event_period=10000)

Attribute STAT/RECV/1/rcu_mask_rw removed!


In [14]:
attrs = archiver.get_subscriber_attributes()
print_periods(attrs)
print()
print_freq(attrs)

Attribute                                     Poll Period     Archive Period 
----------
STAT/RECV/1/ant_mask_rw                       1000            5000           
STAT/RECV/1/state                             1000            5000           
STAT/RECV/1/status                            1000            5000           
STAT/RECV/1/rcu_mask_rw                       1000            10000          

Attribute                                     Record Freq     Failure Freq   
----------
STAT/RECV/1/ant_mask_rw                       0.0             3.0            
STAT/RECV/1/state                             1.0             2.0            
STAT/RECV/1/status                            -1.0            4.0            
STAT/RECV/1/rcu_mask_rw                       1.0             0.0            


In [15]:
# Add SDP attributes to load test
sdp_name = 'STAT/SDP/1'
d2=DeviceProxy(sdp_name) 
state = str(d2.state())
print(state)
archiver.add_attributes_by_device(sdp_name,global_archive_period=5000)

Attribute stat/sdp/1/version_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/opcua_missing_attributes_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_wg_amplitude_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_wg_frequency_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_wg_phase_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_beamlet_output_enable_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_beamlet_output_enable_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_eth_destination_mac_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_eth_destination_mac_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_ip_destination_address_r will no

OFF


Attribute stat/sdp/1/fpga_beamlet_output_scale_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_beamlet_output_scale_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_firmware_version_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_global_node_index_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_hardware_version_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_processing_enable_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_processing_enable_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_sdp_info_antenna_band_index_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_sdp_info_block_period_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_sdp_info_f_adc_r will not be archived because polling 

In [16]:
# Start the SDP device
if state == "OFF":
    d2.set_timeout_millis(10000)#Temporary workaround due to new SPD implementation
    time.sleep(1)
    d2.initialise()
    time.sleep(1)
state = str(d2.state())
if state == "STANDBY":
    d.set_defaults()
    d2.on()
state = str(d2.state())
if state == "ON":
    print("Device is now in ON state")

Device is now in ON state


In [17]:
# Check errors
err_dict = archiver.get_subscriber_errors()
err_dict
#Reminder: MySQL DBMS cannot handle SPD/FPGA_scrap_R attribute probably due to its dimension (8192)

{'tango://databaseds:10000/stat/recv/1/status': 'Storing Error: mysql_stmt_bind_param() failed, err=Buffer type is not supported',
 'tango://databaseds:10000/stat/sdp/1/fpga_scrap_r': 'Read value for attribute FPGA_scrap_R has not been updated',
 'tango://databaseds:10000/stat/sdp/1/fpga_scrap_rw': 'Read value for attribute FPGA_scrap_RW has not been updated',
 'tango://databaseds:10000/stat/sdp/1/fpga_temp_r': 'Read value for attribute FPGA_temp_R has not been updated',
 'tango://databaseds:10000/stat/sdp/1/fpga_weights_r': 'Read value for attribute FPGA_weights_R has not been updated',
 'tango://databaseds:10000/stat/sdp/1/fpga_weights_rw': 'Read value for attribute FPGA_weights_RW has not been updated',
 'tango://databaseds:10000/stat/sdp/1/tr_tod_r': 'Read value for attribute TR_tod_R has not been updated'}

In [18]:
# Check frequencies
attrs = archiver.get_subscriber_attributes()
print_periods(attrs)
print()
print_freq(attrs)

Attribute                                     Poll Period     Archive Period 
----------
STAT/RECV/1/ant_mask_rw                       1000            5000           
STAT/RECV/1/state                             1000            5000           
STAT/RECV/1/status                            1000            5000           
STAT/RECV/1/rcu_mask_rw                       1000            10000          
STAT/SDP/1/fpga_scrap_r                       1000            5000           
STAT/SDP/1/fpga_scrap_rw                      1000            5000           
STAT/SDP/1/fpga_temp_r                        1000            5000           
STAT/SDP/1/fpga_weights_r                     1000            5000           
STAT/SDP/1/fpga_weights_rw                    1000            5000           
STAT/SDP/1/tr_tod_r                           1000            5000           

Attribute                                     Record Freq     Failure Freq   
----------
STAT/RECV/1/ant_mask_rw                  

In [19]:
# Initialise the retriever object and print the archived attributes in the database
retriever = Retriever()
# Attribute chosen to be retrieved
attr_name = 'ant_mask_rw'
attr_fq_name = str(device_name+'/'+attr_name).lower()
attr_fq_name

'stat/recv/1/ant_mask_rw'

In [20]:
# Retrieve records in the last n hours (works even with decimals)

# Use alternatively one of the following two methods to retrieve data (last n hours or interval)
records= retriever.get_attribute_value_by_hours(attr_fq_name,hours=0.1)
#records = retriever.get_attribute_value_by_interval(attr_fq_name,'2021-09-01 16:00:00', '2021-09-01 16:03:00')

if not records:
    print('Empty result!')
else:
    # Convert DB Array records into Python lists
    data = build_array_from_record(records,records[0].dim_x_r)
    # Extract only the value from the array 
    array_values = get_values_from_record(data)

#records
#data
#array_values

In [21]:
data

[[<Array_Boolean_RW(att_conf_id='1',data_time='2021-11-09 11:52:29.957895',recv_time='2021-11-09 11:52:30.955440',insert_time='2021-11-09 11:52:30.957113',idx='0',dim_x_r='3',dim_y_r='32',value_r='1',dim_x_w='3',dim_y_w='32',value_w='1',quality='0',att_error_desc_id='None')>,
  <Array_Boolean_RW(att_conf_id='1',data_time='2021-11-09 11:52:29.957895',recv_time='2021-11-09 11:52:30.955440',insert_time='2021-11-09 11:52:30.957113',idx='1',dim_x_r='3',dim_y_r='32',value_r='1',dim_x_w='3',dim_y_w='32',value_w='1',quality='0',att_error_desc_id='None')>,
  <Array_Boolean_RW(att_conf_id='1',data_time='2021-11-09 11:52:29.957895',recv_time='2021-11-09 11:52:30.955440',insert_time='2021-11-09 11:52:30.957113',idx='2',dim_x_r='3',dim_y_r='32',value_r='1',dim_x_w='3',dim_y_w='32',value_w='1',quality='0',att_error_desc_id='None')>],
 [<Array_Boolean_RW(att_conf_id='1',data_time='2021-11-09 11:52:40.957954',recv_time='2021-11-09 11:52:40.997550',insert_time='2021-11-09 11:52:40.998981',idx='0',dim_x

In [22]:
#archiver.remove_attribute_from_archiver('STAT/recv/1/rcu_temperature_r')
archiver.remove_attributes_in_error()

Attribute stat/recv/1/status removed!
Attribute stat/sdp/1/fpga_scrap_r removed!
Attribute stat/sdp/1/fpga_scrap_rw removed!
Attribute stat/sdp/1/fpga_weights_r removed!
Attribute stat/sdp/1/fpga_weights_rw removed!


In [27]:
# Add a new subscriber if not already present
print(archiver.es_list)
print(archiver.get_next_subscriber())
if len(archiver.es_list)==1:
    archiver.add_event_subscriber()
print(archiver.get_next_subscriber()) # choose the best one with minimum load
new_subscriber = archiver.get_next_subscriber()

['tango://databaseds:10000/archiving/hdbpp/eventsubscriber01']
tango://databaseds:10000/archiving/hdbpp/eventsubscriber01
tango://databaseds:10000/archiving/hdbpp/eventsubscriber01


In [28]:
# Move SDP attributes from one EventSubscriber to another one
archiver.remove_attributes_by_device(sdp_name)
archiver.add_attributes_by_device(sdp_name,global_archive_period=5000,es_name=new_subscriber)

Attribute stat/sdp/1/version_r not found in archiving list!
Attribute stat/sdp/1/opcua_missing_attributes_r not found in archiving list!
Attribute stat/sdp/1/fpga_wg_amplitude_rw not found in archiving list!
Attribute stat/sdp/1/fpga_wg_frequency_rw not found in archiving list!
Attribute stat/sdp/1/fpga_wg_phase_rw not found in archiving list!
Attribute stat/sdp/1/fpga_beamlet_output_enable_r not found in archiving list!
Attribute stat/sdp/1/fpga_beamlet_output_enable_rw not found in archiving list!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_eth_destination_mac_r not found in archiving list!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_eth_destination_mac_rw not found in archiving list!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_ip_destination_address_r not found in archiving list!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_ip_destination_address_rw not found in archiving list!
Attribute stat/sdp/1/fpga_beamlet_output_hdr_udp_destination_port_r not found in archiving list!
Attrib

Attribute stat/sdp/1/fpga_wg_amplitude_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_wg_enable_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_wg_enable_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_wg_frequency_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/fpga_wg_phase_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/tr_fpga_mask_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/tr_fpga_mask_rw will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/tr_fpga_communication_error_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/tr_sdp_config_first_fpga_nr_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/tr_sdp_config_nof_beamsets_r will not be archived because polling is set to FALSE!
Attribute stat/sdp/1/tr_sdp_config_nof_

In [29]:
d.off()
d2.off()